In [1]:
import numpy as np
import pandas as pd
import matplotlib as mpl
import matplotlib.pyplot as plt
import matplotlib.ticker as ticker
from matplotlib.animation import FuncAnimation, FFMpegWriter
from tqdm import tqdm

In [2]:
input_file_path = '../../../siads591 data/processed_data/gabbard/gabbard_7D6.pkl'
freq = '7D'

output_file_path = './gabbard_7D_6I_8K_60_v1.mp4'

In [3]:
bitrate = 1000
dpi = 432*2 # 864 = 8k
fps = 60
use_slice = slice(None, None, None) # 2 ways to slice the data, this is index slicing for the date range

In [4]:
df = pd.read_pickle(f'{input_file_path}')
# df = df[(df.index >= "1980-01-01") & (df.index <= "2021-01-20")] # manually set min/max range based on datetime
# df = df[(df.index >= "2000-10-01") & (df.index <= "2021-01-01")] # manually set min/max range based on datetime
# df = df[(df.index >= "2005-01-01") & (df.index <= "2015-01-01")] # manually set min/max range based on datetime
# df = df[(df.index >= "1974-01-01") & (df.index < "1979-01-01")] # manually set min/max range based on datetime
df = df[(df.index <= "2021-01-28")] # some missing data beyound 1/28

display(df.info())

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 13997992 entries, 1987-12-24 to 2021-01-28
Data columns (total 4 columns):
 #   Column         Dtype 
---  ------         ----- 
 0   NORAD_CAT_ID   uint16
 1   PERIOD_x500    UInt16
 2   APOAPSIS_x20   UInt16
 3   PERIAPSIS_x20  UInt16
dtypes: UInt16(3), uint16(1)
memory usage: 253.6 MB


None

In [5]:
dates = pd.date_range(start=df.index.min(), end=df.index.max(), freq=freq)
dates = dates[use_slice]
print(f'{len(dates)} frames')

3197 frames


In [6]:
## set this to a specific frame number to draw only 1 frame in the notebook to test output
# Set None to generate full video
draw_one_frame = 3196

fig, ax = plt.subplots(dpi=dpi, figsize=(8,5))
fig.set_facecolor("white")
plt.rc('xtick', labelsize=7)
plt.rc('ytick', labelsize=7)


# turns out that you can scale the axis label!
# do that instead of wasting computation time on data conversion
ax.set_xlim(87*500,130*500)
ax.set_ylim(100*20,2750*20)
ticks_x = ticker.FuncFormatter(lambda x, pos: '{0:g}'.format(x/500))
ax.xaxis.set_major_formatter(ticks_x)
ticks_y = ticker.FuncFormatter(lambda x, pos: '{0:g}'.format(x/20))
ax.yaxis.set_major_formatter(ticks_y)

ax.set_xlabel("Orbital Period (min)")
ax.set_ylabel("Altitude (km)")
artists = []
text_artist = []
text_cache = set()

def plot_it(ax,e):
    global df, artists
    
    # get data for frame
    cdf = df[df.index==e]
    apo = ax.scatter(cdf.PERIOD_x500, cdf.APOAPSIS_x20, color='#fe2700', marker='o', edgecolors='none', alpha=0.3, s=0.7, label="Apoapsis")
    peri = ax.scatter(cdf.PERIOD_x500, cdf.PERIAPSIS_x20, color='#038fd5', marker='o', edgecolors='none', alpha=0.3, s=0.7, label="Periapsis")
    plt.legend(loc="upper right", numpoints=1, fontsize=10, markerscale=10)
    return [apo,peri]

def update(f):
    global pbar, artists, yr
    i, date = f
#     ax.set_title(f"{date.month_name()} {date.year} (frame {i})", loc='right')
    ax.set_title(f"{date.month_name()} {date.year}", loc='right')
    for a in artists:
        a.remove()
    artists = plot_it(ax,date)
    if type(draw_one_frame) != int:
        pbar.update(1)

if type(draw_one_frame) == int:
    update((draw_one_frame,dates[draw_one_frame]))
else:
    pbar = tqdm(total=len(dates)+1)
    ani = FuncAnimation(fig, update, list(enumerate(dates)))
    writervideo = FFMpegWriter(fps=fps, bitrate=bitrate)
    ani.save(f'{output_file_path}', writer=writervideo, dpi=dpi)
    pbar.close()